A (bit!) of networks!

In [4]:
import bqplot
import ipywidgets
import pandas as pd

In [5]:
# random node data
node_data = [
    {"label": "Luke Skywalker", "media": "Star Wars", "shape": "rect"},
    {"label": "Jean-Luc Picard", "media": "Star Trek", "shape": "rect"},
    {"label": "Doctor Who", "media": "Doctor Who", "shape": "rect"},
    {"label": "Pikachu", "media": "Detective Pikachu", "shape": "circle"},
]

In [6]:
graph = bqplot.Graph(node_data=node_data, 
                    colors=["red", "red", "red", "red"])

fig = bqplot.Figure(marks=[graph])
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, marks=[Graph(colors=['red', 'red', 'red'…

Add in edge information into my node-link plot:

In [7]:
node_data = [
    {"label": "Luke Skywalker", "media": "Star Wars", "shape": "rect"},
    {"label": "Jean-Luc Picard", "media": "Star Trek", "shape": "rect"},
    {"label": "Doctor Who", "media": "Doctor Who", "shape": "rect"},
    {"label": "Pikachu", "media": "Detective Pikachu", "shape": "circle"},
]

# link the 0th entry (luke skywalker) directionally to both
#. jean-luc picard (1st entry) AND pikachu (3rd entry)
link_data = [{'source':0, 'target': 1}, {'source':0, 'target':3}]

In [8]:
graph = bqplot.Graph(node_data=node_data, link_data =link_data, 
                    colors=["red","red", "red", "red"])

graph.link_type='line' # showing link direction with a straight line
graph.directed = False # turns of any directionality

# by default (and by necessity) the force between nodes is repulsive
graph.charge = -300

fig = bqplot.Figure(marks=[graph])
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, marks=[Graph(charge=-300, colors=['red',…

Add in a tooltip to this graph.

In [9]:
tooltip = bqplot.Tooltip(fields=['media'])
graph = bqplot.Graph(node_data = node_data, link_data = link_data, 
                    colors=['red', 'red', 'red', 'red'],
                    tooltip=tooltip)

fig = bqplot.Figure(marks=[graph])
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, marks=[Graph(colors=['red', 'red', 'red'…

In [10]:
tooltip = bqplot.Tooltip(fields=['media'])
graph = bqplot.Graph(node_data = node_data, link_data = link_data, 
                    colors=['red', 'red', 'red', 'red'],
                    tooltip=tooltip)

# add in a widget printing out the media
label = ipywidgets.Label()

def print_stuff_observation(obj, element):
    label.value = 'Media = ' + element['data']['media']
    
graph.on_element_click(print_stuff_observation)

fig = bqplot.Figure(marks=[graph])
ipywidgets.VBox([label,fig])

Networked data from facebook -- we wil use some subsetting data (sub-networks):

In [77]:
filename = 'facebook_combined_sm000090_000010.txt' # more dispersed network

#filename = 'facebook_combined_sm000030_000000.txt' # one central person

In [78]:
network = pd.read_csv('/Users/jillnaiman/Downloads/'+filename, 
                     sep=' ', names=['ind1','ind2'])

# extra cleaning
network = network.drop_duplicates()

In [79]:
network

ind1  ind2
0      10    67
2      13    21
3      13    26
4      13    56
5      13    59
..    ...   ...
113    73    88
114    75    85
115    80    88
116    82    84
117    83    84

[117 rows x 2 columns]

In [80]:
# build the necessary data for Graph in bqplot:
node_data = [] # label & the shape of each node
link_data = [] # tell us the links between nodes
color_data = [] # color of each node

In [81]:
# add nodes:
import numpy as np

# how many unique nodes do we have?
u_nodes = np.unique( np.append(network['ind1'], network['ind2']) )

node_data = [] # label & the shape of each node
for un in u_nodes:
    node_data.append({'label':str(un), "shape":"circle"})


In [82]:
u_nodes

array([10, 13, 14, 16, 17, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30,
       31, 33, 39, 40, 41, 42, 44, 45, 48, 51, 53, 54, 55, 56, 57, 59, 60,
       61, 62, 63, 65, 66, 67, 69, 72, 73, 75, 76, 77, 79, 80, 82, 83, 84,
       85, 87, 88, 89])

In [83]:
node_data

[{'label': '10', 'shape': 'circle'},
 {'label': '13', 'shape': 'circle'},
 {'label': '14', 'shape': 'circle'},
 {'label': '16', 'shape': 'circle'},
 {'label': '17', 'shape': 'circle'},
 {'label': '19', 'shape': 'circle'},
 {'label': '20', 'shape': 'circle'},
 {'label': '21', 'shape': 'circle'},
 {'label': '22', 'shape': 'circle'},
 {'label': '23', 'shape': 'circle'},
 {'label': '24', 'shape': 'circle'},
 {'label': '25', 'shape': 'circle'},
 {'label': '26', 'shape': 'circle'},
 {'label': '27', 'shape': 'circle'},
 {'label': '28', 'shape': 'circle'},
 {'label': '29', 'shape': 'circle'},
 {'label': '30', 'shape': 'circle'},
 {'label': '31', 'shape': 'circle'},
 {'label': '33', 'shape': 'circle'},
 {'label': '39', 'shape': 'circle'},
 {'label': '40', 'shape': 'circle'},
 {'label': '41', 'shape': 'circle'},
 {'label': '42', 'shape': 'circle'},
 {'label': '44', 'shape': 'circle'},
 {'label': '45', 'shape': 'circle'},
 {'label': '48', 'shape': 'circle'},
 {'label': '51', 'shape': 'circle'},
 

In [84]:
# now specify links -- going from a node to all of its connections
link_data = [] # tell us the links between nodes
color_data = [] # color of each node
for iu,un in enumerate(u_nodes):
    target_ids = network.loc[network['ind1'] == un]
    tnodes = np.unique(target_ids['ind2'].values)
    for t in tnodes: # find index associated with this un
        tind = np.where(t == u_nodes)[0][0]
        link_data.append({'source':iu, 'target':tind})
    color_data.append('blue')

In [85]:
link_data

[{'source': 0, 'target': 39},
 {'source': 1, 'target': 7},
 {'source': 1, 'target': 12},
 {'source': 1, 'target': 30},
 {'source': 1, 'target': 32},
 {'source': 1, 'target': 37},
 {'source': 1, 'target': 39},
 {'source': 1, 'target': 48},
 {'source': 2, 'target': 6},
 {'source': 2, 'target': 14},
 {'source': 2, 'target': 21},
 {'source': 3, 'target': 15},
 {'source': 3, 'target': 48},
 {'source': 4, 'target': 5},
 {'source': 4, 'target': 21},
 {'source': 5, 'target': 21},
 {'source': 5, 'target': 54},
 {'source': 6, 'target': 21},
 {'source': 6, 'target': 23},
 {'source': 7, 'target': 11},
 {'source': 7, 'target': 12},
 {'source': 7, 'target': 17},
 {'source': 7, 'target': 19},
 {'source': 7, 'target': 20},
 {'source': 7, 'target': 29},
 {'source': 7, 'target': 30},
 {'source': 7, 'target': 38},
 {'source': 7, 'target': 39},
 {'source': 7, 'target': 53},
 {'source': 8, 'target': 52},
 {'source': 9, 'target': 26},
 {'source': 9, 'target': 34},
 {'source': 9, 'target': 49},
 {'source': 1

In [86]:
# plot

graph = bqplot.Graph(node_data=node_data, 
                     link_data = link_data,
                    colors=color_data)

# play with these for different graphs
graph.charge = -100 
graph.link_type = 'line'
graph.link_distance=50
# there is no direction to links
graph.directed = False

fig = bqplot.Figure(marks = [graph])
fig.layout.min_width='1000px'
fig.layout.min_height='900px'
# note: I think this has to be the layout for this to look right
fig

# in theory, we could color this network by what school folks are in, or some such
#  but while the dataset does contain some of these features, the 
#  answer rate is too sparse for our subset here

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, layout=Layout(min_height='900px', min_wi…

Below is stuff that Jill messed up in class! You can see what went wrong for fun if you'd like, but the right stuff is posted above :)

(FYI: what went wrong was that I had to refresh my browser for REASONS.  I suspect something with bqplot's packages just got updated during class)

In [22]:
maxNet = max([network['ind1'].max(), network['ind2'].max()])

In [23]:
maxNet

89

In [64]:
node_data = [] # label & the shape of each node

import numpy as np

# unique nodes:
u_nodes = np.unique(np.append(network['ind1'].values, network['ind2'].values))
#for i in range(len(u_nodes)): # individual nodes in the network
for i in range(maxNet+1): # individual nodes in the network
    node_data.append({"label":str(i), "shape":"circle"})    
    #node_data.append({"label":str(u_nodes[i]), "shape":"circle"})

In [65]:
#network['ind1']

In [66]:
#node_data

In [67]:
link_data = [] # tell us the links between nodes
color_data = [] # color of each node

for i in range(len(network)): # link data
    source_id = network.iloc[i]["ind1"]
    target_id = network.iloc[i]["ind2"]
    link_data.append({'source':source_id, 'target': target_id})
    color_data.append('blue')

In [68]:
link_data

[{'source': 10, 'target': 67},
 {'source': 10, 'target': 67},
 {'source': 13, 'target': 21},
 {'source': 13, 'target': 26},
 {'source': 13, 'target': 56},
 {'source': 13, 'target': 59},
 {'source': 13, 'target': 65},
 {'source': 13, 'target': 67},
 {'source': 13, 'target': 82},
 {'source': 14, 'target': 20},
 {'source': 14, 'target': 28},
 {'source': 14, 'target': 41},
 {'source': 16, 'target': 29},
 {'source': 16, 'target': 82},
 {'source': 17, 'target': 19},
 {'source': 17, 'target': 41},
 {'source': 19, 'target': 41},
 {'source': 19, 'target': 89},
 {'source': 20, 'target': 41},
 {'source': 20, 'target': 44},
 {'source': 21, 'target': 25},
 {'source': 21, 'target': 26},
 {'source': 21, 'target': 31},
 {'source': 21, 'target': 39},
 {'source': 21, 'target': 40},
 {'source': 21, 'target': 55},
 {'source': 21, 'target': 56},
 {'source': 21, 'target': 66},
 {'source': 21, 'target': 67},
 {'source': 21, 'target': 88},
 {'source': 22, 'target': 87},
 {'source': 23, 'target': 51},
 {'sourc

In [71]:
graph = bqplot.Graph(node_data = node_data, link_data=link_data, colors=color_data)

graph.charge = -100

fig = bqplot.Figure(marks=[graph])
fig.layout.min_width='1000px'
fig.layout.min_height='900px'
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, layout=Layout(min_height='900px', min_wi…

In [72]:
node_data = []
link_data = []
color_data = [] # all same color

# add nodes
maxNet = max([network['ind1'].max(),network['ind2'].max()])
for i in range(maxNet+1):
    node_data.append({"label": str(i), 'shape_attrs': {'r': 8} }) # small circles
    
# now, make links
for i in range(len(network)):
    # we are linking the ith object to another jth object, but we 
    #  gotta figure out with jth object it is
    source_id = network.iloc[i]['ind1']
    target_id = network.iloc[i]['ind2']
    link_data.append({'source': source_id, 'target': target_id})
    color_data.append('blue')

In [73]:
graph = bqplot.Graph(node_data=node_data, 
                     link_data = link_data,
                    colors=color_data)

# play with these for different graphs
graph.charge = -100 
graph.link_type = 'line'
graph.link_distance=50
# there is no direction to links
graph.directed = False

fig = bqplot.Figure(marks = [graph])
fig.layout.min_width='1000px'
fig.layout.min_height='900px'
# note: I think this has to be the layout for this to look right
fig

Figure(fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, layout=Layout(min_height='900px', min_wi…